In [1]:
import geopandas as gpd
import pandas as pd

edges = gpd.read_file('./data/networks/gipuzkoa_drive_edges_nearest_nodes.geojson')
nodes = gpd.read_file('./data/networks/gipuzkoa_drive_nodes_nearest_nodes.geojson')

print('Edges:', edges.crs)
print('Nodes:', nodes.crs)

Edges: EPSG:4326
Nodes: EPSG:4326


In [2]:
print(nodes.head())
print(edges.head())

    osmid          y         x  street_count highway   ref  \
0  448001  43.179563 -2.489983             3    None  None   
1  448006  43.182655 -2.481422             4    None  None   
2  451289  43.192781 -2.438172             3    None  None   
3  469503  43.191805 -2.451204             3    None  None   
4  469506  43.191796 -2.452494             3    None  None   

                     coords                   geometry  
0  (-2.4899828, 43.1795625)  POINT (-2.48998 43.17956)  
1  (-2.4814224, 43.1826552)  POINT (-2.48142 43.18266)  
2  (-2.4381722, 43.1927813)  POINT (-2.43817 43.19278)  
3   (-2.4512039, 43.191805)    POINT (-2.4512 43.1918)  
4  (-2.4524942, 43.1917959)   POINT (-2.45249 43.1918)  
        u           v  key                            osmid  oneway reversed  \
0  448001  3934729820    0                         44716332   False    False   
1  448001      916343    0                       1009087270   False     True   
2  448006    25433518    0                   

In [3]:
import networkx as nx

# Create a graph from your edges and nodes
G = nx.DiGraph()  # Directed graph if the roads are one-way, or nx.Graph() for undirected

# Add nodes to the graph
for _, row in nodes.iterrows():
    G.add_node(row['osmid'], x=row['x'], y=row['y'])

# Add edges with multiple attributes
for _, row in edges.iterrows():
    u = row['nearest_node_start']
    v = row['nearest_node_end']
    time = row['time_s']
    length = row['length']
    maxspeed = row['maxspeed']
    geometry = row['geometry']
    
    # Add edge with time, length, maxspeed, and geometry
    G.add_edge(u, v, weight=time, length=length, maxspeed=maxspeed, geometry=geometry)

# Set CRS to WGS84 (EPSG:4326) as the coordinates are in latitude and longitude
G.graph['crs'] = 'EPSG:4326'

In [4]:
from scipy.spatial import cKDTree
import numpy as np
from shapely.geometry import Point

# Build the cKDTree for the nodes (for efficient nearest-neighbor search)
nodes['coords'] = list(zip(nodes.geometry.x, nodes.geometry.y))
node_tree = cKDTree(np.array(nodes['coords'].tolist()))

# Function to find nearest node
def get_nearest_node(point):
    dist, index = node_tree.query([point.x, point.y])
    return nodes.iloc[index]['osmid']

In [5]:
o_lon, o_lat=-2.01578381790964,43.304574686941336
#o_lon, o_lat=-1.9820539544817326,43.3196830982974
d_lon, d_lat= -1.9687977669669718, 43.29232181880548

# get nearest nodes
orig_node = get_nearest_node(Point(o_lon, o_lat))
dest_node = get_nearest_node(Point(d_lon, d_lat))

# find the shortest path
route = nx.shortest_path(G, orig_node, dest_node, weight='time_s')

In [6]:
# find the shortest path
route = nx.shortest_path(G, orig_node, dest_node, weight='time_s')

# show total time
total_time = sum([G[u][v]['weight'] for u, v in zip(route[:-1], route[1:])])
print('Total time:', 1.25*total_time, 'seconds')

# time to min (would add a 1.25 coef to account for the average speed, as it is not always the max speed)
total_time = 1.25 * total_time / 60
print('Total time:', total_time, 'minutes')

Total time: 645.6178649999999 seconds
Total time: 10.76029775 minutes


In [7]:
import geopandas as gpd

# Load the geojson file and print to check
building_nodes_gdf = gpd.read_file('./data/geojson/building_nodes_with_poi.geojson')

print(len(building_nodes_gdf))
print(building_nodes_gdf.head())

58768
  Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
0    8594095 -1.948183  43.299723    2135506826             5.202316   
1    8594099 -1.948484  43.299120    2135506826             5.202316   
2    8594100 -1.948365  43.298748    2135506826             5.202316   
3    8796114 -1.928046  43.315046    6548202929             3.369070   
4    8796136 -1.928175  43.313904    6548202929             2.023299   

  block_color nearest_poi  nearest_poi_node                   geometry  
0      yellow     20-0004         457239233  POINT (-1.94818 43.29972)  
1      yellow     20-0004         457239233  POINT (-1.94848 43.29912)  
2      yellow     20-0004         457239233  POINT (-1.94837 43.29875)  
3       green     20-0178         533746770  POINT (-1.92805 43.31505)  
4       green     20-0019         476567754   POINT (-1.92818 43.3139)  


In [8]:
# Fill the time_to_poi column with None
building_nodes_gdf['time_to_nearest_poi'] = None
building_nodes_gdf['block_color'] = None
building_nodes_gdf['nearest_poi'] = None
building_nodes_gdf['nearest_poi_node'] = None
building_nodes_gdf['nearest_node'] = None
print(building_nodes_gdf.head())

  Referencia       lon        lat nearest_node time_to_nearest_poi  \
0    8594095 -1.948183  43.299723         None                None   
1    8594099 -1.948484  43.299120         None                None   
2    8594100 -1.948365  43.298748         None                None   
3    8796114 -1.928046  43.315046         None                None   
4    8796136 -1.928175  43.313904         None                None   

  block_color nearest_poi nearest_poi_node                   geometry  
0        None        None             None  POINT (-1.94818 43.29972)  
1        None        None             None  POINT (-1.94848 43.29912)  
2        None        None             None  POINT (-1.94837 43.29875)  
3        None        None             None  POINT (-1.92805 43.31505)  
4        None        None             None   POINT (-1.92818 43.3139)  


In [9]:
poi = gpd.read_file('./data/poi/estetica.geojson')
poi['lon'] = poi['geometry'].x
poi['lat'] = poi['geometry'].y
print(poi.head())

  IDENTIFICADOR     DENOMINACIÓN DEL ESTABLECIMIENTO              DIRECCIÓN  \
0      L0328934  Kix - Kax Ileapaindegi eta Estetika  Calle Armendi Gain, 1   
1      L0432423                           Peluquería     Calle San Juan, 39   
2      L0310711                Peluquería y estética     Calle San Juan, 30   
3      L0190385               Larraitz Ileapaindegia   Barrio Larraitz, 2-A   
4      L0417371                Kixkur ile-apaindegia    Barrio Larraitz, 14   

    LOCALIDAD  CÓD. POSTAL MUNICIPIO TERRITORIO HISTÓRICO  CNAE  \
0         Aia        20809       Aia             Gipuzkoa  9602   
1      Alegia        20260    Alegia             Gipuzkoa  9602   
2      Alegia        20260    Alegia             Gipuzkoa  9602   
3  Errotaldea        20260    Alegia             Gipuzkoa  9602   
4  Errotaldea        20260    Alegia             Gipuzkoa  9602   

                             DESCRIPCIÓN CNAE ESTRATO EMPLEO  ...  \
0  Peluquería y otros tratamientos de belleza        

In [11]:
def get_nodes(row):
    orig_node = row['nearest_node']
    dest_node=row['nearest_poi_node']

def nearest_node(row):
    if pd.isnull(row['lon']) or pd.isnull(row['lat']):
        return None  

    try:
        nearest_node = get_nearest_node(Point(row['lon'], row['lat']))
        return nearest_node
    except Exception as e:
        print(f"Error en la fila {row.name}: {e}")
        return None  

poi['nearest_node'] = poi.apply(nearest_node, axis=1)
building_nodes_gdf['nearest_node'] = building_nodes_gdf.apply(nearest_node, axis=1)

In [12]:
def nearest_poi(row, poi_df):
    """Find the nearest POI and return its identifier, latitude, and longitude."""
    distances = poi_df['geometry'].apply(lambda x: row.geometry.distance(x))
    nearest = poi_df.loc[distances.idxmin()]
    
    return pd.Series([nearest['DENOMINACIÓN DEL ESTABLECIMIENTO'], nearest.geometry.y, nearest.geometry.x])

# Apply the function to each row and store the results in new columns
building_nodes_gdf[['nearest_poi', 'nearest_poi_lat', 'nearest_poi_lon']] = building_nodes_gdf.apply(nearest_poi, poi_df=poi, axis=1)

# Display the first few rows to check
print(building_nodes_gdf[['nearest_poi', 'nearest_poi_lat', 'nearest_poi_lon']].head())

            nearest_poi  nearest_poi_lat  nearest_poi_lon
0                 Ascen        43.295155        -1.953601
1                 Ascen        43.295155        -1.953601
2                 Ascen        43.295155        -1.953601
3  Peluquería Estíbaliz        43.317034        -1.927933
4  Peluquería Estíbaliz        43.317034        -1.927933


In [13]:
# Get the nearest node of the nearest poi that is already in the poi dataframe
def nearest_poi_node(row):
    nearest_node = poi.loc[row['nearest_poi'] == poi['DENOMINACIÓN DEL ESTABLECIMIENTO']]['nearest_node']
    return nearest_node.values[0]

In [14]:
# Apply the function to each row in the GeoDataFrame
building_nodes_gdf['nearest_poi_node'] = building_nodes_gdf.apply(nearest_poi_node, axis=1)

In [15]:
print(type(building_nodes_gdf))

<class 'geopandas.geodataframe.GeoDataFrame'>


In [16]:
import networkx as nx
import requests

def get_osrm_route(start, end):
    """Fetches the travel time from OSRM if no path is found in the network."""
    url = f"http://router.project-osrm.org/route/v1/driving/{start[1]},{start[0]};{end[1]},{end[0]}?overview=false&steps=true&annotations=duration"
    response = requests.get(url)
    if response.status_code == 200:
        route = response.json()
        return route['routes'][0]['duration'] / 60  # Convert to minutes
    else:
        return None  # Return None if the request fails

def calculate_travel_time(row, G):
    try:
        orig_node = row['nearest_node']
        dest_node = row['nearest_poi_node']
        
        # Compute shortest path based on 'weight' (time in seconds)
        route = nx.shortest_path(G, orig_node, dest_node, weight='weight')
        
        # Compute total travel time along the route
        total_time = sum(G[u][v]['weight'] for u, v in zip(route[:-1], route[1:]))

        if G[u][v]['length']<100:
            total_time += 10
            print('Intersection delay added')
            
        # Convert to minutes
        total_time_minutes = 1.25 * total_time / 60
        print("Time from " +str(row['lat'])+', '+str(row['lon'])+' to '+str(row['nearest_poi'])+' is '+str(total_time_minutes)+'. Row '+str(row.name))

        return total_time_minutes
            
    except nx.NetworkXNoPath:
        # If no path is found, use OSRM API as fallback
        start = (row['lat'], row['lon'])  # Origin coordinates
        end = (row['nearest_poi_lat'], row['nearest_poi_lon'])  # Destination coordinates
        total_time_minutes = get_osrm_route(start, end)  # Fetch from OSRM

        if total_time_minutes is None:
            print(f"Warning: OSRM could not find a route from {start} to {end}. Assigning a default value.")
            return float('inf')  # Or some other fallback value

        return 1.25 * total_time_minutes

In [17]:
# Apply function to each row and create the new column
building_nodes_gdf['time_to_nearest_poi'] = building_nodes_gdf.apply(lambda row: calculate_travel_time(row, G), axis=1)

Intersection delay added
Time from 43.29972301892612, -1.948182651545842 to Ascen is 3.880196458333334. Row 0
Intersection delay added
Time from 43.299120491272, -1.948483617316717 to Ascen is 3.880196458333334. Row 1
Intersection delay added
Time from 43.29874792935789, -1.948365215924241 to Ascen is 3.880196458333334. Row 2
Intersection delay added
Time from 43.31504624311431, -1.928045577056794 to Peluquería Estíbaliz is 0.34984333333333334. Row 3
Intersection delay added
Time from 43.31390356883271, -1.928175198325877 to Peluquería Estíbaliz is 0.34984333333333334. Row 4
Intersection delay added
Time from 43.31423087006452, -1.982315741860613 to La Cubana - Manicura y pedicura is 0.3365108333333333. Row 5
Intersection delay added
Time from 43.31613017399259, -1.919572903775051 to Peluquería y estética is 32.04623358333333. Row 6
Intersection delay added
Time from 43.317170830792605, -1.920829693434758 to Centro estética avanzada Jose Fonfría is 5.741195708333333. Row 7
Intersection

In [18]:
print(building_nodes_gdf.head())

  Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
0    8594095 -1.948183  43.299723     300125529             3.880196   
1    8594099 -1.948484  43.299120     300125529             3.880196   
2    8594100 -1.948365  43.298748     300125529             3.880196   
3    8796114 -1.928046  43.315046     482709764             0.349843   
4    8796136 -1.928175  43.313904     482709764             0.349843   

  block_color           nearest_poi  nearest_poi_node  \
0        None                 Ascen      4.570717e+08   
1        None                 Ascen      4.570717e+08   
2        None                 Ascen      4.570717e+08   
3        None  Peluquería Estíbaliz      6.064007e+09   
4        None  Peluquería Estíbaliz      6.064007e+09   

                    geometry  nearest_poi_lat  nearest_poi_lon  
0  POINT (-1.94818 43.29972)        43.295155        -1.953601  
1  POINT (-1.94848 43.29912)        43.295155        -1.953601  
2  POINT (-1.94837 43.29875) 

In [19]:
# count rows with inf values
print(building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] == float('inf')].shape[0])

# print the rows with inf values
print(building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] == float('inf')])

12
      Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
2699     6793217 -2.174482  43.285190    9218868815                  inf   
2700     6793216 -2.174428  43.285196    9218868815                  inf   
2702     6793215 -2.174334  43.285170    9218868815                  inf   
5445     4784097 -2.417514  43.213677     130175691                  inf   
5446     4784106 -2.417392  43.213584     130175687                  inf   
32585    6792094 -2.173674  43.284834    9218868815                  inf   
32586    6792093 -2.173573  43.284825    9218868815                  inf   
32587    6792092 -2.173441  43.284812    9218868815                  inf   
32602    6792112 -2.174488  43.284731    9218868815                  inf   
39136    4764043 -2.413163  43.032604     571820511                  inf   
50731    6792113 -2.174459  43.284878    9218868815                  inf   
50732    6793220 -2.174422  43.285004    9218868815                  inf   

      bl

In [20]:
import geopandas as gpd
import numpy as np
from scipy.spatial import cKDTree

# Filter rows: separate those with finite values and those with 'inf'
finite_times = building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] != float('inf')]
inf_times = building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] == float('inf')]

# Convert geometries to coordinates (assuming Point geometries)
finite_coords = np.array(list(zip(finite_times.geometry.x, finite_times.geometry.y)))
inf_coords = np.array(list(zip(inf_times.geometry.x, inf_times.geometry.y)))

# Create KDTree from finite values
tree = cKDTree(finite_coords)

# Find the nearest finite value for each 'inf' row
_, nearest_idx = tree.query(inf_coords)

# Store the corrected values in a new column instead of modifying the original
inf_times = inf_times.copy()  # Ensure we don't modify the original DataFrame
inf_times['nearest_valid_time'] = finite_times.iloc[nearest_idx]['time_to_nearest_poi'].values

# Print rows that still have 'inf' values

print(inf_times)

      Referencia       lon        lat  nearest_node  time_to_nearest_poi  \
2699     6793217 -2.174482  43.285190    9218868815                  inf   
2700     6793216 -2.174428  43.285196    9218868815                  inf   
2702     6793215 -2.174334  43.285170    9218868815                  inf   
5445     4784097 -2.417514  43.213677     130175691                  inf   
5446     4784106 -2.417392  43.213584     130175687                  inf   
32585    6792094 -2.173674  43.284834    9218868815                  inf   
32586    6792093 -2.173573  43.284825    9218868815                  inf   
32587    6792092 -2.173441  43.284812    9218868815                  inf   
32602    6792112 -2.174488  43.284731    9218868815                  inf   
39136    4764043 -2.413163  43.032604     571820511                  inf   
50731    6792113 -2.174459  43.284878    9218868815                  inf   
50732    6793220 -2.174422  43.285004    9218868815                  inf   

      block

In [21]:
import geopandas as gpd
import numpy as np
from scipy.spatial import cKDTree

# Define distance threshold (adjust as needed)
distance_threshold = 20  # in meters

# Filter rows: separate those with finite values and those with 'inf'
finite_times = building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] != float('inf')]
inf_times = building_nodes_gdf[building_nodes_gdf['time_to_nearest_poi'] == float('inf')]

# Convert geometries to coordinates (assuming Point geometries in a projected CRS)
finite_coords = np.array(list(zip(finite_times.geometry.x, finite_times.geometry.y)))
inf_coords = np.array(list(zip(inf_times.geometry.x, inf_times.geometry.y)))

# Create KDTree from finite values
tree = cKDTree(finite_coords)

if len(inf_coords) == 0:
    print("No 'inf' coordinates found. Skipping query.")
else:
    # Find the nearest finite value for each 'inf' row
    distances, nearest_idx = tree.query(inf_coords)

    # Get nearest valid time values
    nearest_times = finite_times.iloc[nearest_idx]['time_to_nearest_poi'].values

    # Store the assigned time separately (without modifying the original DataFrame)
    assigned_times = np.where(distances < distance_threshold, 1, nearest_times)

    # Store results in a copy of `inf_times`
    inf_times = inf_times.copy()
    inf_times['nearest_valid_time'] = nearest_times
    inf_times['distance_to_nearest_poi'] = distances
    inf_times['assigned_time'] = assigned_times

In [22]:
# Store the index of the rows in `building_nodes_gdf` that correspond to the 'inf' rows
indexes_to_update = inf_times.index

# Update the original `building_nodes_gdf` at the rows where 'inf' was originally present
building_nodes_gdf.loc[indexes_to_update, 'time_to_nearest_poi'] = assigned_times

# Optionally, display the updated rows to verify the result
print(building_nodes_gdf.loc[indexes_to_update, ['geometry', 'time_to_nearest_poi']])

                        geometry  time_to_nearest_poi
2699   POINT (-2.17448 43.28519)                  1.0
2700    POINT (-2.17443 43.2852)                  1.0
2702   POINT (-2.17433 43.28517)                  1.0
5445   POINT (-2.41751 43.21368)                  1.0
5446   POINT (-2.41739 43.21358)                  1.0
32585  POINT (-2.17367 43.28483)                  1.0
32586  POINT (-2.17357 43.28482)                  1.0
32587  POINT (-2.17344 43.28481)                  1.0
32602  POINT (-2.17449 43.28473)                  1.0
39136   POINT (-2.41316 43.0326)                  1.0
50731  POINT (-2.17446 43.28488)                  1.0
50732    POINT (-2.17442 43.285)                  1.0


In [23]:
# Assign colors to the blocks based on the time it takes to reach the nearest POI
building_nodes_gdf.loc[building_nodes_gdf['time_to_nearest_poi'] < 7, 'block_color'] = '#00572a'  # Dark Green
building_nodes_gdf.loc[(building_nodes_gdf['time_to_nearest_poi'] >= 7) & (building_nodes_gdf['time_to_nearest_poi'] < 15), 'block_color'] = '#7CB342'  # Green
building_nodes_gdf.loc[(building_nodes_gdf['time_to_nearest_poi'] >= 15) & (building_nodes_gdf['time_to_nearest_poi'] < 22), 'block_color'] = '#FFFF00'  # Yellow
building_nodes_gdf.loc[(building_nodes_gdf['time_to_nearest_poi'] >= 22) & (building_nodes_gdf['time_to_nearest_poi'] < 30), 'block_color'] = '#FFA500'  # Orange
building_nodes_gdf.loc[(building_nodes_gdf['time_to_nearest_poi'] >= 30) & (building_nodes_gdf['time_to_nearest_poi'] < 40), 'block_color'] = '#D50000'  # Red
building_nodes_gdf.loc[building_nodes_gdf['time_to_nearest_poi'] >= 40, 'block_color'] = '#8f0340'  # Burgundy
#nodes_gdf.loc[(nodes_gdf['time_to_nearest_poi'] >= 20) & (nodes_gdf['time_to_nearest_poi'] < 25), 'block_color'] = '#8f0340'  # Dark red
#nodes_gdf.loc[nodes_gdf['time_to_nearest_poi'] >= 25, 'block_color'] = '#6a1717'  # Purple

In [24]:
building_nodes_gdf.to_file('./outputs/car/estetica_nodes_times_drive_newcolors.geojson', driver='GeoJSON')